In [ ]:
import pandas as pd
import json
import numpy as np
import spacy
from spacy.lang.en import English
import string
import re

In [ ]:
import json

In [ ]:
!pip install datasets==1.0.2
!pip install transformers
!rm seq2seq_trainer.py
!wget https://raw.githubusercontent.com/huggingface/transformers/master/examples/seq2seq/seq2seq_trainer.py
!pip install rouge_score

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
rm: cannot remove 'seq2seq_trainer.py': No such file or directory
--2022-09-05 22:48:36--  https://raw.githubusercontent.com/huggingface/transformers/master/examples/seq2seq/seq2seq_trainer.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 404 Not Found
2022-09-05 22:48:36 ERROR 404: Not Found.

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import datasets
import transformers
import pandas as pd
from datasets import Dataset

In [ ]:
from transformers import EncoderDecoderModel
from transformers import  Seq2SeqTrainer,Seq2SeqTrainingArguments
from transformers import TrainingArguments
from dataclasses import dataclass, field
from typing import Optional

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
s_val_path = '/content/drive/MyDrive/corpus (1)/val.json'
s_test_path = '/content/drive/MyDrive/corpus (1)/test.json'
s_train_path = '/content/drive/MyDrive/corpus (1)/train.json'

In [ ]:
def read_samsum_dataset(path):
  with open(path) as in_file:
	  data = json.load(in_file)
  return data

In [ ]:
s_val = read_samsum_dataset(s_val_path)

In [ ]:
s_test = read_samsum_dataset(s_test_path)

In [ ]:
s_train = read_samsum_dataset(s_train_path)

In [ ]:
s_train_data = pd.DataFrame(s_train)
s_val_data = pd.DataFrame(s_val)
s_test_data = pd.DataFrame(s_test)

In [ ]:
#s_test_data = pd.DataFrame(s_test)
s_test_data.head()

id                                            summary  \
0  13862856  Hannah needs Betty's number but Amanda doesn't...   
1  13729565  Eric and Rob are going to watch a stand-up on ...   
2  13680171  Lenny can't decide which trousers to buy. Bob ...   
3  13729438  Emma will be home soon and she will let Will k...   
4  13828600  Jane is in Warsaw. Ollie and Jane has a party....   

                                            dialogue  
0  Hannah: Hey, do you have Betty's number?\nAman...  
1  Eric: MACHINE!\r\nRob: That's so gr8!\r\nEric:...  
2  Lenny: Babe, can you help me with something?\r...  
3  Will: hey babe, what do you want for dinner to...  
4  Ollie: Hi , are you in Warsaw\r\nJane: yes, ju...

In [ ]:
s_train_data['dialogue'] = s_train_data['dialogue'].str.replace('\r', '')
s_train_data['dialogue'] = s_train_data['dialogue'].str.replace('\n', '')
s_train_data['summary'] = s_train_data['summary'].str.replace('\r', '')
s_train_data['summary'] = s_train_data['summary'].str.replace('\n', '')

In [ ]:
s_val_data['dialogue'] = s_val_data['dialogue'].str.replace('\r', '')
s_val_data['dialogue'] = s_val_data['dialogue'].str.replace('\n', '')
s_val_data['summary'] = s_val_data['summary'].str.replace('\r', '')
s_val_data['summary'] = s_val_data['summary'].str.replace('\n', '')

In [ ]:
s_train_data.head()

id                                            summary  \
0  13818513  Amanda baked cookies and will bring Jerry some...   
1  13728867  Olivia and Olivier are voting for liberals in ...   
2  13681000  Kim may try the pomodoro technique recommended...   
3  13730747  Edward thinks he is in love with Bella. Rachel...   
4  13728094  Sam is confused, because he overheard Rick com...   

                                            dialogue  
0  Amanda: I baked  cookies. Do you want some?Jer...  
1  Olivia: Who are you voting for in this electio...  
2  Tim: Hi, what's up?Kim: Bad mood tbh, I was go...  
3  Edward: Rachel, I think I'm in ove with Bella....  
4  Sam: hey  overheard rick say somethingSam: i d...

In [ ]:
s_train_data = s_train_data[:3000]

In [ ]:
s_val_data = s_val_data[:1500]

cnn dataset

In [ ]:
c_val_path = '/content/drive/MyDrive/cnn_dailymail/validation.csv'
c_test_path = '/content/drive/MyDrive/cnn_dailymail/test.csv'
c_train_path = '/content/drive/MyDrive/cnn_dailymail/train.csv'

In [ ]:
import pandas as pd

In [ ]:
def read_cnn_dataset(path):
  with open(path) as in_file:
	  data = pd.read_csv(in_file)
  return data

In [ ]:
c_val= read_cnn_dataset(c_val_path)

In [ ]:
c_test= read_cnn_dataset(c_test_path)

In [ ]:
c_train= read_cnn_dataset(c_train_path)

In [ ]:
c_train_data = pd.DataFrame(c_train)
c_val_data = pd.DataFrame(c_val)
c_test_data = pd.DataFrame(c_test)

In [ ]:
c_test_data = pd.DataFrame(c_test)
c_test_data.head()

id  \
0  92c514c913c0bdfe25341af9fd72b29db544099b   
1  2003841c7dc0e7c5b1a248f9cd536d727f27a45a   
2  91b7d2311527f5c2b63a65ca98d21d9c92485149   
3  caabf9cbdf96eb1410295a673e953d304391bfbb   
4  3da746a7d9afcaa659088c8366ef6347fe6b53ea   

                                             article  \
0  Ever noticed how plane seats appear to be gett...   
1  A drunk teenage boy had to be rescued by secur...   
2  Dougie Freedman is on the verge of agreeing a ...   
3  Liverpool target Neto is also wanted by PSG an...   
4  Bruce Jenner will break his silence in a two-h...   

                                          highlights  
0  Experts question if  packed out planes are put...  
1  Drunk teenage boy climbed into lion enclosure ...  
2  Nottingham Forest are close to extending Dougi...  
3  Fiorentina goalkeeper Neto has been linked wit...  
4  Tell-all interview with the reality TV star, 6...

In [ ]:
c_train_data.head()

id  \
0  0001d1afc246a7964130f43ae940af6bc6c57f01   
1  0002095e55fcbd3a2f366d9bf92a95433dc305ef   
2  00027e965c8264c35cc1bc55556db388da82b07f   
3  0002c17436637c4fe1837c935c04de47adb18e9a   
4  0003ad6ef0c37534f80b55b4235108024b407f0b   

                                             article  \
0  By . Associated Press . PUBLISHED: . 14:11 EST...   
1  (CNN) -- Ralph Mata was an internal affairs li...   
2  A drunk driver who killed a young woman in a h...   
3  (CNN) -- With a breezy sweep of his pen Presid...   
4  Fleetwood are the only team still to have a 10...   

                                          highlights  
0  Bishop John Folda, of North Dakota, is taking ...  
1  Criminal complaint: Cop used his role to help ...  
2  Craig Eccleston-Todd, 27, had drunk at least t...  
3  Nina dos Santos says Europe must be ready to a...  
4  Fleetwood top of League One after 2-0 win at S...

In [ ]:
c_train_data = c_train_data[:3000]

In [ ]:
c_val_data = c_val_data[:1500]

In [ ]:
c_train_data.rename(columns={'article': 'text','highlights':'summary'}, inplace= True)

In [ ]:
c_train_data.head()

id  \
0  0001d1afc246a7964130f43ae940af6bc6c57f01   
1  0002095e55fcbd3a2f366d9bf92a95433dc305ef   
2  00027e965c8264c35cc1bc55556db388da82b07f   
3  0002c17436637c4fe1837c935c04de47adb18e9a   
4  0003ad6ef0c37534f80b55b4235108024b407f0b   

                                                text  \
0  By . Associated Press . PUBLISHED: . 14:11 EST...   
1  (CNN) -- Ralph Mata was an internal affairs li...   
2  A drunk driver who killed a young woman in a h...   
3  (CNN) -- With a breezy sweep of his pen Presid...   
4  Fleetwood are the only team still to have a 10...   

                                             summary  
0  Bishop John Folda, of North Dakota, is taking ...  
1  Criminal complaint: Cop used his role to help ...  
2  Craig Eccleston-Todd, 27, had drunk at least t...  
3  Nina dos Santos says Europe must be ready to a...  
4  Fleetwood top of League One after 2-0 win at S...

In [ ]:
c_val_data.rename(columns={'article': 'text','highlights':'summary'}, inplace= True)

In [ ]:
c_val_data.head()

id  \
0  61df4979ac5fcc2b71be46ed6fe5a46ce7f071c3   
1  21c0bd69b7e7df285c3d1b1cf56d4da925980a68   
2  56f340189cd128194b2e7cb8c26bb900e3a848b4   
3  00a665151b89a53e5a08a389df8334f4106494c2   
4  9f6fbd3c497c4d28879bebebea220884f03eb41a   

                                                text  \
0  Sally Forrest, an actress-dancer who graced th...   
1  A middle-school teacher in China has inked hun...   
2  A man convicted of killing the father and sist...   
3  Avid rugby fan Prince Harry could barely watch...   
4  A Triple M Radio producer has been inundated w...   

                                             summary  
0  Sally Forrest, an actress-dancer who graced th...  
1  Works include pictures of Presidential Palace ...  
2  Iftekhar Murtaza, 29, was convicted a year ago...  
3  Prince Harry in attendance for England's crunc...  
4  Nick Slater's colleagues uploaded a picture to...

In [ ]:
c_test_data.rename(columns={'article': 'text','highlights':'summary'}, inplace= True)

In [ ]:
c_test_data.head()

id  \
0  92c514c913c0bdfe25341af9fd72b29db544099b   
1  2003841c7dc0e7c5b1a248f9cd536d727f27a45a   
2  91b7d2311527f5c2b63a65ca98d21d9c92485149   
3  caabf9cbdf96eb1410295a673e953d304391bfbb   
4  3da746a7d9afcaa659088c8366ef6347fe6b53ea   

                                                text  \
0  Ever noticed how plane seats appear to be gett...   
1  A drunk teenage boy had to be rescued by secur...   
2  Dougie Freedman is on the verge of agreeing a ...   
3  Liverpool target Neto is also wanted by PSG an...   
4  Bruce Jenner will break his silence in a two-h...   

                                             summary  
0  Experts question if  packed out planes are put...  
1  Drunk teenage boy climbed into lion enclosure ...  
2  Nottingham Forest are close to extending Dougi...  
3  Fiorentina goalkeeper Neto has been linked wit...  
4  Tell-all interview with the reality TV star, 6...

In [ ]:
s_train_data.rename(columns={'dialouge': 'text'}, inplace= True)

In [ ]:
s_train_data = s_train_data[['id','dialogue','summary']]
s_train_data.head()

KeyError: ignored

In [ ]:
s_train_data.rename(columns={'dialogue': 'text','summary':'summary'}, inplace= True)

In [ ]:
s_train_data.head()

id                                               text  \
0  13818513  Amanda: I baked  cookies. Do you want some?Jer...   
1  13728867  Olivia: Who are you voting for in this electio...   
2  13681000  Tim: Hi, what's up?Kim: Bad mood tbh, I was go...   
3  13730747  Edward: Rachel, I think I'm in ove with Bella....   
4  13728094  Sam: hey  overheard rick say somethingSam: i d...   

                                             summary  
0  Amanda baked cookies and will bring Jerry some...  
1  Olivia and Olivier are voting for liberals in ...  
2  Kim may try the pomodoro technique recommended...  
3  Edward thinks he is in love with Bella. Rachel...  
4  Sam is confused, because he overheard Rick com...

In [ ]:
s_val_data = s_val_data[['id','dialogue','summary']]
s_val_data.head()

id                                           dialogue  \
0  13817023  A: Hi Tom, are you busy tomorrow’s afternoon?B...   
1  13716628  Emma: I’ve just fallen in love with this adven...   
2  13829420  Jackie: Madison is pregnantJackie: but she doe...   
3  13819648  Marla: <file_photo>Marla: look what I found un...   
4  13728448  Robert: Hey give me the address of this music ...   

                                             summary  
0  A will go to the animal shelter tomorrow to ge...  
1  Emma and Rob love the advent calendar. Lauren ...  
2  Madison is pregnant but she doesn't want to ta...  
3        Marla found a pair of boxers under her bed.  
4  Robert wants Fred to send him the address of t...

In [ ]:
s_val_data.rename(columns={'dialogue': 'text','summary':'summary'}, inplace= True)

In [ ]:
s_test_data = s_test_data[['id','dialogue','summary']]
s_test_data.head()

id                                           dialogue  \
0  13862856  Hannah: Hey, do you have Betty's number?\nAman...   
1  13729565  Eric: MACHINE!\r\nRob: That's so gr8!\r\nEric:...   
2  13680171  Lenny: Babe, can you help me with something?\r...   
3  13729438  Will: hey babe, what do you want for dinner to...   
4  13828600  Ollie: Hi , are you in Warsaw\r\nJane: yes, ju...   

                                             summary  
0  Hannah needs Betty's number but Amanda doesn't...  
1  Eric and Rob are going to watch a stand-up on ...  
2  Lenny can't decide which trousers to buy. Bob ...  
3  Emma will be home soon and she will let Will k...  
4  Jane is in Warsaw. Ollie and Jane has a party....

In [ ]:
s_test_data.rename(columns={'dialogue': 'text','summary':'summary'}, inplace= True)

In [ ]:
s_test_data.head()

id                                            summary  \
0  13862856  Hannah needs Betty's number but Amanda doesn't...   
1  13729565  Eric and Rob are going to watch a stand-up on ...   
2  13680171  Lenny can't decide which trousers to buy. Bob ...   
3  13729438  Emma will be home soon and she will let Will k...   
4  13828600  Jane is in Warsaw. Ollie and Jane has a party....   

                                                text  
0  Hannah: Hey, do you have Betty's number?\nAman...  
1  Eric: MACHINE!\r\nRob: That's so gr8!\r\nEric:...  
2  Lenny: Babe, can you help me with something?\r...  
3  Will: hey babe, what do you want for dinner to...  
4  Ollie: Hi , are you in Warsaw\r\nJane: yes, ju...

In [ ]:
display(s_train_data.shape,c_train_data.shape)

(3000, 3)

(3000, 3)

In [ ]:
merged_train = pd.concat([s_train_data,c_train_data])

In [ ]:
merged_train.head()

id                                               text  \
0  13818513  Amanda: I baked  cookies. Do you want some?Jer...   
1  13728867  Olivia: Who are you voting for in this electio...   
2  13681000  Tim: Hi, what's up?Kim: Bad mood tbh, I was go...   
3  13730747  Edward: Rachel, I think I'm in ove with Bella....   
4  13728094  Sam: hey  overheard rick say somethingSam: i d...   

                                             summary  
0  Amanda baked cookies and will bring Jerry some...  
1  Olivia and Olivier are voting for liberals in ...  
2  Kim may try the pomodoro technique recommended...  
3  Edward thinks he is in love with Bella. Rachel...  
4  Sam is confused, because he overheard Rick com...

In [ ]:
display(merged_train.shape)

(6000, 3)

In [ ]:
from sklearn.utils import shuffle


In [ ]:
merged_train = shuffle(merged_train)

In [ ]:
merged_val= pd.concat([s_val_data,c_val_data])

In [ ]:
merged_val.head()

id                                               text  \
0  13817023  A: Hi Tom, are you busy tomorrow’s afternoon?B...   
1  13716628  Emma: I’ve just fallen in love with this adven...   
2  13829420  Jackie: Madison is pregnantJackie: but she doe...   
3  13819648  Marla: <file_photo>Marla: look what I found un...   
4  13728448  Robert: Hey give me the address of this music ...   

                                             summary  
0  A will go to the animal shelter tomorrow to ge...  
1  Emma and Rob love the advent calendar. Lauren ...  
2  Madison is pregnant but she doesn't want to ta...  
3        Marla found a pair of boxers under her bed.  
4  Robert wants Fred to send him the address of t...

In [ ]:
merged_val = shuffle(merged_val)

In [ ]:
display(merged_val.shape)

(2318, 3)

In [ ]:
merged_test = pd.concat([s_test_data,c_test_data])

In [ ]:
merged_test = shuffle(merged_test)

In [ ]:
display(merged_test.shape)

(12309, 3)

In [ ]:
from datasets import Dataset
train_data=Dataset.from_pandas(merged_train)
val_data = Dataset.from_pandas(merged_val)
test_data = Dataset.from_pandas(merged_test)

In [ ]:
model_checkpoint = "facebook/bart-large-xsum" 

In [ ]:
from datasets import load_dataset, load_metric

In [ ]:
metric = load_metric("rouge")

In [ ]:
from transformers import AutoTokenizer
    
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)

In [ ]:
max_input_length = 512
max_target_length = 128

def preprocess_function(examples):
    inputs = [doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=max_input_length, truncation=True)

    # Setup the tokenizer for targets
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=max_target_length, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

In [ ]:
train_tokenized_datasets = train_data.map(preprocess_function, batched=True)

  0%|          | 0/6 [00:00<?, ?ba/s]

In [ ]:
val_tokenized_datasets = val_data.map(preprocess_function, batched=True)

  0%|          | 0/3 [00:00<?, ?ba/s]

In [ ]:
from transformers import AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer
from transformers import pipeline 
import torch
from transformers import BartTokenizer, BartForConditionalGeneration

In [ ]:
model = BartForConditionalGeneration.from_pretrained(model_checkpoint)

In [ ]:
batch_size = 8
args = Seq2SeqTrainingArguments(
    "test-dialogue-summarization",
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    gradient_accumulation_steps=2,
    weight_decay=0.01,
    save_total_limit=2,
    num_train_epochs=3,
    predict_with_generate=True,
    logging_steps=1
    #fp16=True
)

In [ ]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

In [ ]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    # Replace -100 in the labels as we can't decode them.
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
    
    # Rouge expects a newline after each sentence
    decoded_preds = ["\n".join(nltk.sent_tokenize(pred.strip())) for pred in decoded_preds]
    decoded_labels = ["\n".join(nltk.sent_tokenize(label.strip())) for label in decoded_labels]
    
    result = metric.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)
    # Extract a few results
    result = {key: value.mid.fmeasure * 100 for key, value in result.items()}
    
    # Add mean generated length
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)
    
    return {k: round(v, 4) for k, v in result.items()}

In [ ]:
trainer = Seq2SeqTrainer(
    model,
    args,
    train_dataset=train_tokenized_datasets,
    eval_dataset=val_tokenized_datasets,
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [ ]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: __index_level_0__, summary, id, text. If __index_level_0__, summary, id, text are not expected by `BartForConditionalGeneration.forward`,  you can safely ignore this message.
/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,
***** Running training *****
  Num examples = 6000
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 2
  Total optimization steps = 1125


The following columns in the evaluation set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: __index_level_0__, summary, id, text. If __index_level_0__, summary, id, text are not expected by `BartForConditionalGeneration.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 2318
  Batch size = 8
Saving model checkpoint to test-dialogue-summarization/checkpoint-500
Configuration saved in test-dialogue-summarization/checkpoint-500/config.json
Model weights saved in test-dialogue-summarization/checkpoint-500/pytorch_model.bin
tokenizer config file saved in test-dialogue-summarization/checkpoint-500/tokenizer_config.json
Special tokens file saved in test-dialogue-summarization/checkpoint-500/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: __index_level_0__, summary, id, text. If 

TrainOutput(global_step=1125, training_loss=1.483747603416443, metrics={'train_runtime': 7193.6357, 'train_samples_per_second': 2.502, 'train_steps_per_second': 0.156, 'total_flos': 1.944744432481075e+16, 'train_loss': 1.483747603416443, 'epoch': 3.0})

In [ ]:
trainer.evaluate()

The following columns in the evaluation set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: __index_level_0__, summary, id, text. If __index_level_0__, summary, id, text are not expected by `BartForConditionalGeneration.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 2318
  Batch size = 8


{'eval_loss': 1.697027564048767,
 'eval_rouge1': 44.9725,
 'eval_rougeL': 33.4391,
 'eval_gen_len': 50.1562,
 'eval_runtime': 1075.7968,
 'eval_samples_per_second': 2.155,
 'eval_steps_per_second': 0.27,
 'epoch': 3.0}

In [ ]:
import torch

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [ ]:
merged_test.values.tolist()

[['f6172a1e869f9a709401cad64d7c10dd435f7328',
  "Zara Phillips has revealed how she got her fitness back after the birth of her first child Mia - by hitting the exercise bike every morning before her daughter even woke up. The 33-year-old, who is vying for a place on Team GB at the Rio Olympics, welcomed Mia Grace with husband Mike Tindall last year. But after finding herself 'surprised' by how her fitness dropped during pregnancy, the Queen's granddaughter has committed to a strict exercise and diet regime to get back in shape. Scroll down for video . Zara Phillips has told of how she was surprised at how difficult it was to regain her fitness after the birth of her daughter, Mia, one (pictured left in January and right, last July when Mia was six months old) 'What surprised me about having a baby is losing all your fitness and how tough it is to get it back to that level again,' she said in an interview with The Sunday Time Magazine. Starting her morning at 7am, Zara has a breakfast 

In [ ]:
for i in merged_test:
  print(merged_test['summary'])


214      The Queen's granddaughter is vying for a spot ...
206      The spectacular photos were taken at paddy fie...
507      Lynn and Diana are disgusted by sugar babies, ...
3922     Manchester United have Robin van Persie back f...
11044    Epiphany Morgan and Carl Mason produced 365 do...
                               ...                        
2447     Mai Zizhou has been trained to play basketball...
4849     Chelsea sealed a 1-0 victory against Mancheste...
11460    The attack at a Garissa university last week k...
6377     Jon Flanagan's contract expires in the summer ...
9014     "The Muppets" might return to television on AB...
Name: summary, Length: 12309, dtype: object
214      The Queen's granddaughter is vying for a spot ...
206      The spectacular photos were taken at paddy fie...
507      Lynn and Diana are disgusted by sugar babies, ...
3922     Manchester United have Robin van Persie back f...
11044    Epiphany Morgan and Carl Mason produced 365 do...
            

In [ ]:
merged_test['text']= pandas.Series(merged_test['text'], dtype="string")


In [ ]:
merged_test.loc[:,'text'] = merged_test.loc[:, 'text'].astype(str)

In [ ]:
type(merged_test['text'])

pandas.core.series.Series